This code is aiming for finding more signature genes, such that we can distinguish T cell CD8 and T cell CD4.  
First, we need to build a pseudo data set, with training and testing.  
The previous 10000 samples only contains 144 signatures, we deprecate it and start a new one with 20000 genes.  

In [1]:
import pandas as pd
import numpy as np

In [2]:
df_six_sample = pd.read_csv('../Transcriptomics reporting/rna_immune_cell_sample.tsv', sep='\t')
df_six_sample

Sample ID Donor        Immune cell          ENSG ID        Gene name  \
0              940     a         eosinophil  ENSG00000000003           TSPAN6   
1              940     a         eosinophil  ENSG00000000005             TNMD   
2              940     a         eosinophil  ENSG00000000419             DPM1   
3              940     a         eosinophil  ENSG00000000457            SCYL3   
4              940     a         eosinophil  ENSG00000000460         C1orf112   
...            ...   ...                ...              ...              ...   
2197653       1051     f  memory CD4 T-cell  ENSG00000291313  ENSG00000291313   
2197654       1051     f  memory CD4 T-cell  ENSG00000291314  ENSG00000291314   
2197655       1051     f  memory CD4 T-cell  ENSG00000291315  ENSG00000291315   
2197656       1051     f  memory CD4 T-cell  ENSG00000291316  ENSG00000291316   
2197657       1051     f  memory CD4 T-cell  ENSG00000291317          TMEM276   

             TPM     pTPM     nTPM  
0         0.0397   0.0493   0.0542  
1         0.0000   0.0000   0.0000  
2        16.8694  20.9751  23.0553  
3         7.2059   8.9597   9.8483  
4         0.0000   0.0000   0.0000  
...          ...      ...      ...  
2197653   1.1818   1.4218   1.2565  
2197654   0.0000   0.0000   0.0000  
2197655   0.0000   0.0000   0.0000  
2197656   0.8999   1.0826   0.9567  
2197657  11.1273  13.3869  11.8304  

[2197658 rows x 8 columns]

In [3]:
set(df_six_sample['Immune cell'])

{'MAIT T-cell',
 'NK-cell',
 'T-reg',
 'basophil',
 'classical monocyte',
 'eosinophil',
 'gdT-cell',
 'intermediate monocyte',
 'memory B-cell',
 'memory CD4 T-cell',
 'memory CD8 T-cell',
 'myeloid DC',
 'naive B-cell',
 'naive CD4 T-cell',
 'naive CD8 T-cell',
 'neutrophil',
 'non-classical monocyte',
 'plasmacytoid DC',
 'total PBMC'}

In [4]:
df_neutrophil_a = df_six_sample[(df_six_sample['Donor']=='a') & (df_six_sample['Immune cell']=='neutrophil')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_a"})
df_neutrophil_b = df_six_sample[(df_six_sample['Donor']=='b') & (df_six_sample['Immune cell']=='neutrophil')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_b"})
df_neutrophil_c = df_six_sample[(df_six_sample['Donor']=='c') & (df_six_sample['Immune cell']=='neutrophil')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_c"})
df_neutrophil_d = df_six_sample[(df_six_sample['Donor']=='d') & (df_six_sample['Immune cell']=='neutrophil')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_d"})
df_neutrophil_e = df_six_sample[(df_six_sample['Donor']=='e') & (df_six_sample['Immune cell']=='neutrophil')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_e"})
df_neutrophil_f = df_six_sample[(df_six_sample['Donor']=='f') & (df_six_sample['Immune cell']=='neutrophil')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_f"})

df_neutrophil = df_neutrophil_a.copy()
df_neutrophil = df_neutrophil.merge(df_neutrophil_b, on='Gene Stable ID')
df_neutrophil = df_neutrophil.merge(df_neutrophil_c, on='Gene Stable ID')
df_neutrophil = df_neutrophil.merge(df_neutrophil_d, on='Gene Stable ID')
df_neutrophil = df_neutrophil.merge(df_neutrophil_e, on='Gene Stable ID')
df_neutrophil = df_neutrophil.merge(df_neutrophil_f, on='Gene Stable ID')
df_neutrophil

Gene Stable ID    TPM_a   TPM_b   TPM_c    TPM_d    TPM_e    TPM_f
0      ENSG00000000003   0.1203  0.0769  0.2775   0.2618   0.3372   0.0935
1      ENSG00000000005   0.0000  0.0000  0.0000   0.0000   0.0000   0.0000
2      ENSG00000000419  22.6895  7.7639  8.0804  10.2188  13.7181  11.3185
3      ENSG00000000457   5.8098  4.9903  3.8067   3.7820   6.1861   2.1125
4      ENSG00000000460   0.0170  0.0133  0.0000   0.5556   0.0000   0.1424
...                ...      ...     ...     ...      ...      ...      ...
20157  ENSG00000291313   2.6432  3.2233  0.0003   0.7954   0.5334   0.7479
20158  ENSG00000291314   0.0000  0.0000  0.0000   0.0000   0.0000   0.0000
20159  ENSG00000291315   0.0000  0.0000  0.0000   0.0000   0.0000   0.0000
20160  ENSG00000291316   1.8453  1.9087  3.0812   3.6778   1.7268   1.8208
20161  ENSG00000291317   0.3152  0.0163  3.4575   0.0798   0.5074   1.5464

[20162 rows x 7 columns]

In [5]:
df_basophil_c = df_six_sample[(df_six_sample['Donor']=='c') & (df_six_sample['Immune cell']=='basophil')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_c"})
df_basophil_d = df_six_sample[(df_six_sample['Donor']=='d') & (df_six_sample['Immune cell']=='basophil')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_d"})
df_basophil_e = df_six_sample[(df_six_sample['Donor']=='e') & (df_six_sample['Immune cell']=='basophil')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_e"})
df_basophil_f = df_six_sample[(df_six_sample['Donor']=='f') & (df_six_sample['Immune cell']=='basophil')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_f"})

df_basophil = df_basophil_c.copy()
df_basophil = df_basophil.merge(df_basophil_d, on='Gene Stable ID')
df_basophil = df_basophil.merge(df_basophil_e, on='Gene Stable ID')
df_basophil = df_basophil.merge(df_basophil_f, on='Gene Stable ID')
df_basophil

Gene Stable ID    TPM_c    TPM_d   TPM_e    TPM_f
0      ENSG00000000003   0.1881   0.3209  0.2396   0.0292
1      ENSG00000000005   0.0000   0.0000  0.0000   0.0000
2      ENSG00000000419  10.0856  21.5354  0.0318  11.1024
3      ENSG00000000457  11.0216  25.8686  0.8258   0.6748
4      ENSG00000000460   2.8822   0.0106  0.0000   5.2716
...                ...      ...      ...     ...      ...
20157  ENSG00000291313   6.4225   0.6163  0.6735  25.6292
20158  ENSG00000291314   0.0000   0.0000  0.0000   0.0000
20159  ENSG00000291315   0.0000   0.0000  0.0000   0.0000
20160  ENSG00000291316   3.4807   0.0000  0.0000   6.5336
20161  ENSG00000291317   0.0225   0.1137  0.0864   0.0487

[20162 rows x 5 columns]

In [6]:
df_eosinophil_a = df_six_sample[(df_six_sample['Donor']=='a') & (df_six_sample['Immune cell']=='eosinophil')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_a"})
df_eosinophil_b = df_six_sample[(df_six_sample['Donor']=='b') & (df_six_sample['Immune cell']=='eosinophil')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_b"})
df_eosinophil_c = df_six_sample[(df_six_sample['Donor']=='c') & (df_six_sample['Immune cell']=='eosinophil')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_c"})
df_eosinophil_d = df_six_sample[(df_six_sample['Donor']=='d') & (df_six_sample['Immune cell']=='eosinophil')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_d"})
df_eosinophil_e = df_six_sample[(df_six_sample['Donor']=='e') & (df_six_sample['Immune cell']=='eosinophil')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_e"})
df_eosinophil_f = df_six_sample[(df_six_sample['Donor']=='f') & (df_six_sample['Immune cell']=='eosinophil')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_f"})

df_eosinophil = df_eosinophil_a.copy()
df_eosinophil = df_eosinophil.merge(df_eosinophil_b, on='Gene Stable ID')
df_eosinophil = df_eosinophil.merge(df_eosinophil_c, on='Gene Stable ID')
df_eosinophil = df_eosinophil.merge(df_eosinophil_d, on='Gene Stable ID')
df_eosinophil = df_eosinophil.merge(df_eosinophil_e, on='Gene Stable ID')
df_eosinophil = df_eosinophil.merge(df_eosinophil_f, on='Gene Stable ID')
df_eosinophil

Gene Stable ID    TPM_a    TPM_b    TPM_c    TPM_d   TPM_e   TPM_f
0      ENSG00000000003   0.0397   0.0325   0.0804   0.0647  0.0611  0.0705
1      ENSG00000000005   0.0000   0.0000   0.0000   0.0000  0.0000  0.0000
2      ENSG00000000419  16.8694  20.3954  22.1815  11.8845  9.9890  8.4134
3      ENSG00000000457   7.2059   8.7569  12.1146   5.9267  5.9575  2.2893
4      ENSG00000000460   0.0000   2.1868   0.5447   0.5331  1.8150  0.2103
...                ...      ...      ...      ...      ...     ...     ...
20157  ENSG00000291313   7.5118   8.7206   8.1219   2.0013  0.7598  0.2714
20158  ENSG00000291314   0.0000   0.0000   0.0000   0.0000  0.0000  0.0000
20159  ENSG00000291315   0.0000   0.0000   0.0000   0.0000  0.0000  0.0000
20160  ENSG00000291316   3.9983   2.5928   0.0000   2.4306  1.9668  3.0414
20161  ENSG00000291317   0.4925   2.6214   0.0000   4.9222  1.9931  7.6371

[20162 rows x 7 columns]

In [7]:
df_Treg_a = df_six_sample[(df_six_sample['Donor']=='a') & (df_six_sample['Immune cell']=='T-reg')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_a"})
df_Treg_b = df_six_sample[(df_six_sample['Donor']=='b') & (df_six_sample['Immune cell']=='T-reg')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_b"})
df_Treg_c = df_six_sample[(df_six_sample['Donor']=='c') & (df_six_sample['Immune cell']=='T-reg')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_c"})
df_Treg_d = df_six_sample[(df_six_sample['Donor']=='d') & (df_six_sample['Immune cell']=='T-reg')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_d"})
df_Treg_e = df_six_sample[(df_six_sample['Donor']=='e') & (df_six_sample['Immune cell']=='T-reg')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_e"})
df_Treg_f = df_six_sample[(df_six_sample['Donor']=='f') & (df_six_sample['Immune cell']=='T-reg')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_f"})

df_Treg = df_Treg_a.copy()
df_Treg = df_Treg.merge(df_Treg_b, on='Gene Stable ID')
df_Treg = df_Treg.merge(df_Treg_c, on='Gene Stable ID')
df_Treg = df_Treg.merge(df_Treg_d, on='Gene Stable ID')
df_Treg = df_Treg.merge(df_Treg_e, on='Gene Stable ID')
df_Treg = df_Treg.merge(df_Treg_f, on='Gene Stable ID')
df_Treg

Gene Stable ID    TPM_a    TPM_b    TPM_c    TPM_d    TPM_e    TPM_f
0      ENSG00000000003   0.0373   0.0000   0.0772   0.0677   0.0908   0.0171
1      ENSG00000000005   0.0000   0.0000   0.0000   0.0000   0.0000   0.0000
2      ENSG00000000419  33.9186  10.4731  16.5397  17.1776  16.2979  12.7169
3      ENSG00000000457  13.0451   0.5979   3.1278   5.0377  10.3336  10.7121
4      ENSG00000000460   2.2666   0.2929   0.3067   0.9137   0.2490   0.3112
...                ...      ...      ...      ...      ...      ...      ...
20157  ENSG00000291313   1.2751   3.8229   8.6722   4.5812   0.1552   2.1332
20158  ENSG00000291314   0.0000   0.0000   0.0000   0.0000   0.0000   0.0000
20159  ENSG00000291315   0.0000   0.0000   0.0000   0.0000   0.0000   0.0000
20160  ENSG00000291316   0.3046   0.0479   0.0065   0.0122   1.3178   0.0257
20161  ENSG00000291317   4.0564   4.0788   1.2699   4.2047   4.8255   5.9615

[20162 rows x 7 columns]

In [8]:
df_naive_CD4_a = df_six_sample[(df_six_sample['Donor']=='a') & (df_six_sample['Immune cell']=='naive CD4 T-cell')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_a"})
df_naive_CD4_b = df_six_sample[(df_six_sample['Donor']=='b') & (df_six_sample['Immune cell']=='naive CD4 T-cell')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_b"})
df_naive_CD4_c = df_six_sample[(df_six_sample['Donor']=='c') & (df_six_sample['Immune cell']=='naive CD4 T-cell')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_c"})
df_naive_CD4_d = df_six_sample[(df_six_sample['Donor']=='d') & (df_six_sample['Immune cell']=='naive CD4 T-cell')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_d"})
df_naive_CD4_e = df_six_sample[(df_six_sample['Donor']=='e') & (df_six_sample['Immune cell']=='naive CD4 T-cell')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_e"})
df_naive_CD4_f = df_six_sample[(df_six_sample['Donor']=='f') & (df_six_sample['Immune cell']=='naive CD4 T-cell')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_f"})

df_naive_CD4 = df_naive_CD4_a.copy()
df_naive_CD4 = df_naive_CD4.merge(df_naive_CD4_b, on='Gene Stable ID')
df_naive_CD4 = df_naive_CD4.merge(df_naive_CD4_c, on='Gene Stable ID')
df_naive_CD4 = df_naive_CD4.merge(df_naive_CD4_d, on='Gene Stable ID')
df_naive_CD4 = df_naive_CD4.merge(df_naive_CD4_e, on='Gene Stable ID')
df_naive_CD4 = df_naive_CD4.merge(df_naive_CD4_f, on='Gene Stable ID')
df_naive_CD4

Gene Stable ID    TPM_a    TPM_b    TPM_c    TPM_d    TPM_e    TPM_f
0      ENSG00000000003   1.7450   1.2161   2.2648   2.0720   2.1258   2.0402
1      ENSG00000000005   0.0000   0.0000   0.0000   0.0000   0.0000   0.0000
2      ENSG00000000419  36.7716  11.2326  11.4807  17.0749  14.0324  18.3575
3      ENSG00000000457   7.3831   2.4896   3.9798   8.2934   8.6707   7.4562
4      ENSG00000000460   0.2970   0.9514   0.0255   0.0859   0.0063   0.2671
...                ...      ...      ...      ...      ...      ...      ...
20157  ENSG00000291313   1.6315   8.0784   3.4786   5.9375   3.8541   3.8928
20158  ENSG00000291314   0.0000   0.0000   0.0000   0.0000   0.0000   0.0000
20159  ENSG00000291315   0.0000   0.0000   0.0000   0.0000   0.0000   0.0000
20160  ENSG00000291316   0.3068   1.3471   0.4749   0.3547   0.8067   0.7693
20161  ENSG00000291317  10.1920  15.6009  23.1161  21.8874  17.6471  24.8604

[20162 rows x 7 columns]

In [9]:
df_naive_CD8_a = df_six_sample[(df_six_sample['Donor']=='a') & (df_six_sample['Immune cell']=='naive CD8 T-cell')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_a"})
df_naive_CD8_b = df_six_sample[(df_six_sample['Donor']=='b') & (df_six_sample['Immune cell']=='naive CD8 T-cell')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_b"})
df_naive_CD8_c = df_six_sample[(df_six_sample['Donor']=='c') & (df_six_sample['Immune cell']=='naive CD8 T-cell')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_c"})
df_naive_CD8_d = df_six_sample[(df_six_sample['Donor']=='d') & (df_six_sample['Immune cell']=='naive CD8 T-cell')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_d"})
df_naive_CD8_e = df_six_sample[(df_six_sample['Donor']=='e') & (df_six_sample['Immune cell']=='naive CD8 T-cell')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_e"})
df_naive_CD8_f = df_six_sample[(df_six_sample['Donor']=='f') & (df_six_sample['Immune cell']=='naive CD8 T-cell')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_f"})

df_naive_CD8 = df_naive_CD8_a.copy()
df_naive_CD8 = df_naive_CD8.merge(df_naive_CD8_b, on='Gene Stable ID')
df_naive_CD8 = df_naive_CD8.merge(df_naive_CD8_c, on='Gene Stable ID')
df_naive_CD8 = df_naive_CD8.merge(df_naive_CD8_d, on='Gene Stable ID')
df_naive_CD8 = df_naive_CD8.merge(df_naive_CD8_e, on='Gene Stable ID')
df_naive_CD8 = df_naive_CD8.merge(df_naive_CD8_f, on='Gene Stable ID')
df_naive_CD8

Gene Stable ID    TPM_a    TPM_b    TPM_c    TPM_d    TPM_e    TPM_f
0      ENSG00000000003   1.8268   0.9208   1.2003   1.2942   0.1589   1.3775
1      ENSG00000000005   0.0000   0.0000   0.0000   0.0000   0.0000   0.0000
2      ENSG00000000419  31.4337  20.4949  13.4159  14.0075  24.2086  22.8826
3      ENSG00000000457   5.2415   1.8747   7.1193   3.6698   6.0590   9.5438
4      ENSG00000000460   0.3050   0.0000   0.9724   0.7662   1.4071   0.0000
...                ...      ...      ...      ...      ...      ...      ...
20157  ENSG00000291313   1.8196  14.2750   1.5921  10.2641   1.2946   4.5748
20158  ENSG00000291314   0.0000   0.0000   0.0000   0.0000   0.0000   0.0000
20159  ENSG00000291315   0.0000   0.0000   0.0000   0.0000   0.0000   0.0000
20160  ENSG00000291316   0.7166   0.0040   0.8618   1.5199   0.9635   0.5183
20161  ENSG00000291317   9.1243  15.3623  10.7376  11.6384   4.8213  13.4984

[20162 rows x 7 columns]

In [10]:
df_memory_CD4_a = df_six_sample[(df_six_sample['Donor']=='a') & (df_six_sample['Immune cell']=='memory CD4 T-cell')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_a"})
df_memory_CD4_b = df_six_sample[(df_six_sample['Donor']=='b') & (df_six_sample['Immune cell']=='memory CD4 T-cell')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_b"})
df_memory_CD4_c = df_six_sample[(df_six_sample['Donor']=='c') & (df_six_sample['Immune cell']=='memory CD4 T-cell')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_c"})
df_memory_CD4_d = df_six_sample[(df_six_sample['Donor']=='d') & (df_six_sample['Immune cell']=='memory CD4 T-cell')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_d"})
df_memory_CD4_e = df_six_sample[(df_six_sample['Donor']=='e') & (df_six_sample['Immune cell']=='memory CD4 T-cell')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_e"})
df_memory_CD4_f = df_six_sample[(df_six_sample['Donor']=='f') & (df_six_sample['Immune cell']=='memory CD4 T-cell')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_f"})

df_memory_CD4 = df_memory_CD4_a.copy()
df_memory_CD4 = df_memory_CD4.merge(df_memory_CD4_b, on='Gene Stable ID')
df_memory_CD4 = df_memory_CD4.merge(df_memory_CD4_c, on='Gene Stable ID')
df_memory_CD4 = df_memory_CD4.merge(df_memory_CD4_d, on='Gene Stable ID')
df_memory_CD4 = df_memory_CD4.merge(df_memory_CD4_e, on='Gene Stable ID')
df_memory_CD4 = df_memory_CD4.merge(df_memory_CD4_f, on='Gene Stable ID')
df_memory_CD4

Gene Stable ID    TPM_a    TPM_b    TPM_c    TPM_d    TPM_e    TPM_f
0      ENSG00000000003   0.9111   0.9079   0.6807   0.0972   0.7062   1.1781
1      ENSG00000000005   0.0000   0.0000   0.0000   0.0000   0.0000   0.0000
2      ENSG00000000419  29.3998  10.5798  13.0437  13.5442  19.8646  20.2123
3      ENSG00000000457   7.6064   4.8214  11.8280   7.7838   5.9179   8.0693
4      ENSG00000000460   0.4675   0.0000   1.0425   0.9404   0.7339   0.9887
...                ...      ...      ...      ...      ...      ...      ...
20157  ENSG00000291313   0.9608  16.0605   2.7487   6.7457   4.4435   1.1818
20158  ENSG00000291314   0.0000   0.0000   0.0000   0.0000   0.0000   0.0000
20159  ENSG00000291315   0.0000   0.0000   0.0000   0.0000   0.0000   0.0000
20160  ENSG00000291316   0.3652   0.3340   0.9373   0.5405   0.6296   0.8999
20161  ENSG00000291317   8.2209  13.6881   8.2195  10.7392   9.8269  11.1273

[20162 rows x 7 columns]

In [11]:
df_memory_CD8_a = df_six_sample[(df_six_sample['Donor']=='a') & (df_six_sample['Immune cell']=='memory CD8 T-cell')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_a"})
df_memory_CD8_b = df_six_sample[(df_six_sample['Donor']=='b') & (df_six_sample['Immune cell']=='memory CD8 T-cell')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_b"})
df_memory_CD8_c = df_six_sample[(df_six_sample['Donor']=='c') & (df_six_sample['Immune cell']=='memory CD8 T-cell')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_c"})
df_memory_CD8_d = df_six_sample[(df_six_sample['Donor']=='d') & (df_six_sample['Immune cell']=='memory CD8 T-cell')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_d"})
df_memory_CD8_f = df_six_sample[(df_six_sample['Donor']=='f') & (df_six_sample['Immune cell']=='memory CD8 T-cell')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_f"})

df_memory_CD8 = df_memory_CD8_a.copy()
df_memory_CD8 = df_memory_CD8.merge(df_memory_CD8_b, on='Gene Stable ID')
df_memory_CD8 = df_memory_CD8.merge(df_memory_CD8_c, on='Gene Stable ID')
df_memory_CD8 = df_memory_CD8.merge(df_memory_CD8_d, on='Gene Stable ID')
df_memory_CD8 = df_memory_CD8.merge(df_memory_CD8_f, on='Gene Stable ID')
df_memory_CD8

Gene Stable ID    TPM_a    TPM_b    TPM_c    TPM_d    TPM_f
0      ENSG00000000003   1.0946   0.0707   0.0771   0.3995   0.0480
1      ENSG00000000005   0.0000   0.0000   0.0000   0.0000   0.0000
2      ENSG00000000419  23.9668  14.2368  11.2858  16.9963  22.5622
3      ENSG00000000457   6.2126   6.7797   5.9591   3.1876  12.6845
4      ENSG00000000460   1.0396   0.0000   0.5394   1.6257   0.3525
...                ...      ...      ...      ...      ...      ...
20157  ENSG00000291313   0.8075  14.3854   3.2277   7.8611   8.9662
20158  ENSG00000291314   0.0000   0.0000   0.0000   0.0000   0.0000
20159  ENSG00000291315   0.0000   0.0000   0.0000   0.0000   0.0000
20160  ENSG00000291316   0.5600   1.3116   0.4054   0.2613   0.1095
20161  ENSG00000291317   4.7310   2.9555  10.8571   6.5748  10.5172

[20162 rows x 6 columns]

In [12]:
df_memory_B_a = df_six_sample[(df_six_sample['Donor']=='a') & (df_six_sample['Immune cell']=='memory B-cell')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_a"})
df_memory_B_b = df_six_sample[(df_six_sample['Donor']=='b') & (df_six_sample['Immune cell']=='memory B-cell')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_b"})
df_memory_B_c = df_six_sample[(df_six_sample['Donor']=='c') & (df_six_sample['Immune cell']=='memory B-cell')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_c"})
df_memory_B_d = df_six_sample[(df_six_sample['Donor']=='d') & (df_six_sample['Immune cell']=='memory B-cell')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_d"})
df_memory_B_e = df_six_sample[(df_six_sample['Donor']=='e') & (df_six_sample['Immune cell']=='memory B-cell')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_e"})
df_memory_B_f = df_six_sample[(df_six_sample['Donor']=='f') & (df_six_sample['Immune cell']=='memory B-cell')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_f"})

df_memory_B = df_memory_B_a.copy()
df_memory_B = df_memory_B.merge(df_memory_B_b, on='Gene Stable ID')
df_memory_B = df_memory_B.merge(df_memory_B_c, on='Gene Stable ID')
df_memory_B = df_memory_B.merge(df_memory_B_d, on='Gene Stable ID')
df_memory_B = df_memory_B.merge(df_memory_B_e, on='Gene Stable ID')
df_memory_B = df_memory_B.merge(df_memory_B_f, on='Gene Stable ID')
df_memory_B

Gene Stable ID    TPM_a    TPM_b   TPM_c    TPM_d    TPM_e    TPM_f
0      ENSG00000000003   0.2514   0.0205  0.1180   0.0307   0.0422   0.0479
1      ENSG00000000005   0.0000   0.0000  0.0000   0.0000   0.0000   0.0000
2      ENSG00000000419  24.3233  13.3413  1.5761  12.8197   9.6838  17.1621
3      ENSG00000000457   5.7286   4.4139  1.7570   6.5514   5.0394   4.4141
4      ENSG00000000460   0.7692   0.8536  1.6537   1.3110   0.2454   0.4227
...                ...      ...      ...     ...      ...      ...      ...
20157  ENSG00000291313   2.3149  17.6659  8.1803   2.6057   2.6953   0.7809
20158  ENSG00000291314   0.0000   0.0000  0.0000   0.0000   0.0000   0.0000
20159  ENSG00000291315   0.0000   0.0000  0.0000   0.0000   0.0000   0.0000
20160  ENSG00000291316   0.2159   0.4037  0.5611   0.7929   0.4680   0.0093
20161  ENSG00000291317   7.2311   6.7418  0.0134  10.7018  10.9169  16.7942

[20162 rows x 7 columns]

In [13]:
df_naive_B_a = df_six_sample[(df_six_sample['Donor']=='a') & (df_six_sample['Immune cell']=='naive B-cell')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_a"})
df_naive_B_b = df_six_sample[(df_six_sample['Donor']=='b') & (df_six_sample['Immune cell']=='naive B-cell')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_b"})
df_naive_B_c = df_six_sample[(df_six_sample['Donor']=='c') & (df_six_sample['Immune cell']=='naive B-cell')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_c"})
df_naive_B_d = df_six_sample[(df_six_sample['Donor']=='d') & (df_six_sample['Immune cell']=='naive B-cell')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_d"})
df_naive_B_e = df_six_sample[(df_six_sample['Donor']=='e') & (df_six_sample['Immune cell']=='naive B-cell')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_e"})
df_naive_B_f = df_six_sample[(df_six_sample['Donor']=='f') & (df_six_sample['Immune cell']=='naive B-cell')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_f"})

df_naive_B = df_naive_B_a.copy()
df_naive_B = df_naive_B.merge(df_naive_B_b, on='Gene Stable ID')
df_naive_B = df_naive_B.merge(df_naive_B_c, on='Gene Stable ID')
df_naive_B = df_naive_B.merge(df_naive_B_d, on='Gene Stable ID')
df_naive_B = df_naive_B.merge(df_naive_B_e, on='Gene Stable ID')
df_naive_B = df_naive_B.merge(df_naive_B_f, on='Gene Stable ID')
df_naive_B

Gene Stable ID    TPM_a    TPM_b   TPM_c    TPM_d    TPM_e    TPM_f
0      ENSG00000000003   0.1016   0.0613  0.0264   0.2099   0.1147   0.0567
1      ENSG00000000005   0.0000   0.0000  0.0000   0.0000   0.0000   0.0000
2      ENSG00000000419  18.7096   8.7782  5.5059  13.4276  13.7364  14.8953
3      ENSG00000000457   4.9030   5.2318  4.3508   3.4515   6.0347   3.1025
4      ENSG00000000460   0.5152   0.8421  1.6133   1.3517   1.1100   0.2889
...                ...      ...      ...     ...      ...      ...      ...
20157  ENSG00000291313   3.0756  15.1519  7.6780   3.0829   5.0385   4.3791
20158  ENSG00000291314   0.0000   0.0000  0.0000   0.0000   0.0000   0.0000
20159  ENSG00000291315   0.0000   0.0000  0.0000   0.0000   0.0000   0.0000
20160  ENSG00000291316   0.6304   0.7659  0.6324   0.5509   0.3713   0.7798
20161  ENSG00000291317   9.2729  11.6066  7.0841  11.2948   6.8773  12.3149

[20162 rows x 7 columns]

In [14]:
df_classical_monocyte_a = df_six_sample[(df_six_sample['Donor']=='a') & (df_six_sample['Immune cell']=='classical monocyte')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_a"})
df_classical_monocyte_b = df_six_sample[(df_six_sample['Donor']=='b') & (df_six_sample['Immune cell']=='classical monocyte')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_b"})
df_classical_monocyte_c = df_six_sample[(df_six_sample['Donor']=='c') & (df_six_sample['Immune cell']=='classical monocyte')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_c"})
df_classical_monocyte_d = df_six_sample[(df_six_sample['Donor']=='d') & (df_six_sample['Immune cell']=='classical monocyte')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_d"})
df_classical_monocyte_e = df_six_sample[(df_six_sample['Donor']=='e') & (df_six_sample['Immune cell']=='classical monocyte')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_e"})
df_classical_monocyte_f = df_six_sample[(df_six_sample['Donor']=='f') & (df_six_sample['Immune cell']=='classical monocyte')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_f"})

df_classical_monocyte = df_classical_monocyte_a.copy()
df_classical_monocyte = df_classical_monocyte.merge(df_classical_monocyte_b, on='Gene Stable ID')
df_classical_monocyte = df_classical_monocyte.merge(df_classical_monocyte_c, on='Gene Stable ID')
df_classical_monocyte = df_classical_monocyte.merge(df_classical_monocyte_d, on='Gene Stable ID')
df_classical_monocyte = df_classical_monocyte.merge(df_classical_monocyte_e, on='Gene Stable ID')
df_classical_monocyte = df_classical_monocyte.merge(df_classical_monocyte_f, on='Gene Stable ID')
df_classical_monocyte

Gene Stable ID    TPM_a    TPM_b   TPM_c    TPM_d    TPM_e    TPM_f
0      ENSG00000000003   0.0123   0.0187  0.0237   0.1150   0.0405   0.0342
1      ENSG00000000005   0.0000   0.0000  0.0000   0.0000   0.0000   0.0000
2      ENSG00000000419  12.0790  15.1115  9.9823  12.6634  14.2581  12.5436
3      ENSG00000000457   1.9248   2.7023  2.7925   1.8661   3.6163   2.4683
4      ENSG00000000460   0.4821   0.6419  1.0636   0.3839   0.4146   1.1616
...                ...      ...      ...     ...      ...      ...      ...
20157  ENSG00000291313   1.0830  11.2381  3.0096   2.7551   2.1956   4.2757
20158  ENSG00000291314   0.0000   0.0000  0.0000   0.0000   0.0000   0.0000
20159  ENSG00000291315   0.0000   0.0000  0.0000   0.0000   0.0000   0.0000
20160  ENSG00000291316   0.3716   1.0578  0.7780   1.6596   0.4097   1.3847
20161  ENSG00000291317   2.9871   9.9183  7.3322  10.1726   9.1812  12.8919

[20162 rows x 7 columns]

In [15]:
df_intermediate_monocyte_a = df_six_sample[(df_six_sample['Donor']=='a') & (df_six_sample['Immune cell']=='intermediate monocyte')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_a"})
df_intermediate_monocyte_b = df_six_sample[(df_six_sample['Donor']=='b') & (df_six_sample['Immune cell']=='intermediate monocyte')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_b"})
df_intermediate_monocyte_c = df_six_sample[(df_six_sample['Donor']=='c') & (df_six_sample['Immune cell']=='intermediate monocyte')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_c"})
df_intermediate_monocyte_d = df_six_sample[(df_six_sample['Donor']=='d') & (df_six_sample['Immune cell']=='intermediate monocyte')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_d"})
df_intermediate_monocyte_e = df_six_sample[(df_six_sample['Donor']=='e') & (df_six_sample['Immune cell']=='intermediate monocyte')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_e"})
df_intermediate_monocyte_f = df_six_sample[(df_six_sample['Donor']=='f') & (df_six_sample['Immune cell']=='intermediate monocyte')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_f"})

df_intermediate_monocyte = df_intermediate_monocyte_a.copy()
df_intermediate_monocyte = df_intermediate_monocyte.merge(df_intermediate_monocyte_b, on='Gene Stable ID')
df_intermediate_monocyte = df_intermediate_monocyte.merge(df_intermediate_monocyte_c, on='Gene Stable ID')
df_intermediate_monocyte = df_intermediate_monocyte.merge(df_intermediate_monocyte_d, on='Gene Stable ID')
df_intermediate_monocyte = df_intermediate_monocyte.merge(df_intermediate_monocyte_e, on='Gene Stable ID')
df_intermediate_monocyte = df_intermediate_monocyte.merge(df_intermediate_monocyte_f, on='Gene Stable ID')
df_intermediate_monocyte

Gene Stable ID    TPM_a    TPM_b    TPM_c    TPM_d    TPM_e    TPM_f
0      ENSG00000000003   0.0446   0.0391   0.0341   0.0628   0.0973   0.0105
1      ENSG00000000005   0.0000   0.0000   0.0000   0.0000   0.0000   0.0000
2      ENSG00000000419  19.5523  12.7664  10.5568  16.4483  16.2190  17.6875
3      ENSG00000000457   3.7131   3.1264   3.4239   2.8584   2.1687   1.2567
4      ENSG00000000460   4.4266   1.0322   0.4888   0.5974   2.7744   1.0882
...                ...      ...      ...      ...      ...      ...      ...
20157  ENSG00000291313   4.9320   9.2384   4.5343   4.5176   0.6084   4.4578
20158  ENSG00000291314   0.0000   0.0000   0.0000   0.0000   0.0000   0.0000
20159  ENSG00000291315   0.0000   0.0000   0.0000   0.0000   0.0000   0.0000
20160  ENSG00000291316   1.4483   0.7787   0.8639   0.0533   0.7544   0.7378
20161  ENSG00000291317   2.8087   5.5255   5.7700   4.4167   4.4939  10.4791

[20162 rows x 7 columns]

In [16]:
df_non_classical_monocyte_a = df_six_sample[(df_six_sample['Donor']=='a') & (df_six_sample['Immune cell']=='non-classical monocyte')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_a"})
df_non_classical_monocyte_c = df_six_sample[(df_six_sample['Donor']=='c') & (df_six_sample['Immune cell']=='non-classical monocyte')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_c"})
df_non_classical_monocyte_d = df_six_sample[(df_six_sample['Donor']=='d') & (df_six_sample['Immune cell']=='non-classical monocyte')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_d"})
df_non_classical_monocyte_e = df_six_sample[(df_six_sample['Donor']=='e') & (df_six_sample['Immune cell']=='non-classical monocyte')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_e"})
df_non_classical_monocyte_f = df_six_sample[(df_six_sample['Donor']=='f') & (df_six_sample['Immune cell']=='non-classical monocyte')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_f"})

df_non_classical_monocyte = df_non_classical_monocyte_a.copy()
df_non_classical_monocyte = df_non_classical_monocyte.merge(df_non_classical_monocyte_c, on='Gene Stable ID')
df_non_classical_monocyte = df_non_classical_monocyte.merge(df_non_classical_monocyte_d, on='Gene Stable ID')
df_non_classical_monocyte = df_non_classical_monocyte.merge(df_non_classical_monocyte_e, on='Gene Stable ID')
df_non_classical_monocyte = df_non_classical_monocyte.merge(df_non_classical_monocyte_f, on='Gene Stable ID')
df_non_classical_monocyte

Gene Stable ID    TPM_a    TPM_c    TPM_d    TPM_e    TPM_f
0      ENSG00000000003   0.0600   0.0398   0.1495   0.0946   0.0506
1      ENSG00000000005   0.0000   0.0000   0.0000   0.0000   0.0000
2      ENSG00000000419  23.8080  16.7301   0.3436  21.6867  17.7669
3      ENSG00000000457   5.0291   5.2550   1.0221   2.6615   1.9633
4      ENSG00000000460   3.8481   3.0915   0.0000   2.0187   1.2217
...                ...      ...      ...      ...      ...      ...
20157  ENSG00000291313   3.1994   2.9702   0.6908   0.8696   4.2860
20158  ENSG00000291314   0.0000   0.0000   0.0000   0.0000   0.0000
20159  ENSG00000291315   0.0000   0.0000   0.0000   0.0000   0.0000
20160  ENSG00000291316   1.0129   0.3302   0.0078   1.0763   2.1278
20161  ENSG00000291317   2.9663   6.2279  12.4265   5.3278   5.2504

[20162 rows x 6 columns]

In [17]:
df_NK_a = df_six_sample[(df_six_sample['Donor']=='a') & (df_six_sample['Immune cell']=='NK-cell')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_a"})
df_NK_b = df_six_sample[(df_six_sample['Donor']=='b') & (df_six_sample['Immune cell']=='NK-cell')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_b"})
df_NK_c = df_six_sample[(df_six_sample['Donor']=='c') & (df_six_sample['Immune cell']=='NK-cell')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_c"})
df_NK_d = df_six_sample[(df_six_sample['Donor']=='d') & (df_six_sample['Immune cell']=='NK-cell')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_d"})
df_NK_e = df_six_sample[(df_six_sample['Donor']=='e') & (df_six_sample['Immune cell']=='NK-cell')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_e"})
df_NK_f = df_six_sample[(df_six_sample['Donor']=='f') & (df_six_sample['Immune cell']=='NK-cell')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_f"})

df_NK = df_NK_a.copy()
df_NK = df_NK.merge(df_NK_b, on='Gene Stable ID')
df_NK = df_NK.merge(df_NK_c, on='Gene Stable ID')
df_NK = df_NK.merge(df_NK_d, on='Gene Stable ID')
df_NK = df_NK.merge(df_NK_e, on='Gene Stable ID')
df_NK = df_NK.merge(df_NK_f, on='Gene Stable ID')
df_NK

Gene Stable ID    TPM_a    TPM_b    TPM_c    TPM_d    TPM_e    TPM_f
0      ENSG00000000003   0.0798   0.0096   0.1526   0.1192   0.7668   0.0247
1      ENSG00000000005   0.0000   0.0000   0.0000   0.0000   0.0000   0.0000
2      ENSG00000000419  37.4799   8.0522  18.0123  14.7927  36.4722  11.2906
3      ENSG00000000457  18.2780  12.5047   9.9983  10.9192   5.2546   9.9464
4      ENSG00000000460   1.1079   0.5793   1.8122   0.9611  10.2341   0.6801
...                ...      ...      ...      ...      ...      ...      ...
20157  ENSG00000291313   1.3500  12.9522   2.9622  10.0538   1.0198   8.5049
20158  ENSG00000291314   0.0000   0.0000   0.0000   0.0000   0.0000   0.0000
20159  ENSG00000291315   4.5657   0.0000   0.0000   0.0000   0.0000   0.0000
20160  ENSG00000291316   0.1917   0.1937   1.1039   0.0041   0.0000   0.0210
20161  ENSG00000291317   5.9344   9.2987   2.0641   2.6646   0.1120  10.2179

[20162 rows x 7 columns]

In [18]:
df_MAIT_a = df_six_sample[(df_six_sample['Donor']=='a') & (df_six_sample['Immune cell']=='MAIT T-cell')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_a"})
df_MAIT_b = df_six_sample[(df_six_sample['Donor']=='b') & (df_six_sample['Immune cell']=='MAIT T-cell')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_b"})
df_MAIT_c = df_six_sample[(df_six_sample['Donor']=='c') & (df_six_sample['Immune cell']=='MAIT T-cell')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_c"})
df_MAIT_d = df_six_sample[(df_six_sample['Donor']=='d') & (df_six_sample['Immune cell']=='MAIT T-cell')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_d"})
df_MAIT_e = df_six_sample[(df_six_sample['Donor']=='e') & (df_six_sample['Immune cell']=='MAIT T-cell')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_e"})
df_MAIT_f = df_six_sample[(df_six_sample['Donor']=='f') & (df_six_sample['Immune cell']=='MAIT T-cell')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_f"})

df_MAIT = df_MAIT_a.copy()
df_MAIT = df_MAIT.merge(df_MAIT_b, on='Gene Stable ID')
df_MAIT = df_MAIT.merge(df_MAIT_c, on='Gene Stable ID')
df_MAIT = df_MAIT.merge(df_MAIT_d, on='Gene Stable ID')
df_MAIT = df_MAIT.merge(df_MAIT_e, on='Gene Stable ID')
df_MAIT = df_MAIT.merge(df_MAIT_f, on='Gene Stable ID')
df_MAIT

Gene Stable ID    TPM_a    TPM_b    TPM_c    TPM_d    TPM_e    TPM_f
0      ENSG00000000003   1.1002   1.9095   0.9470   0.4849   0.1576   1.7228
1      ENSG00000000005   0.0000   0.0000   0.0000   0.0000   0.0000   0.0000
2      ENSG00000000419  30.4976  15.0839  13.8720  19.6532  14.1778  24.3321
3      ENSG00000000457   8.5448   9.7858   6.0228   6.3088   5.4367  12.9848
4      ENSG00000000460   0.1056   0.8479   0.1872   0.6586   1.0566   0.0000
...                ...      ...      ...      ...      ...      ...      ...
20157  ENSG00000291313   3.8579   3.7650   6.8434   4.3637   2.3253   8.0710
20158  ENSG00000291314   0.0000   0.0000   0.0000   0.0000   0.0000   0.0000
20159  ENSG00000291315   0.0000   0.0000   0.0000   0.0000   0.0000   0.0000
20160  ENSG00000291316   1.2957   0.2813   1.9438   0.7772   0.2633   0.1638
20161  ENSG00000291317  14.1568  15.3220  14.7635  10.6184  12.6565  17.3129

[20162 rows x 7 columns]

In [19]:
df_gdT_a = df_six_sample[(df_six_sample['Donor']=='a') & (df_six_sample['Immune cell']=='gdT-cell')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_a"})
df_gdT_b = df_six_sample[(df_six_sample['Donor']=='b') & (df_six_sample['Immune cell']=='gdT-cell')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_b"})
df_gdT_c = df_six_sample[(df_six_sample['Donor']=='c') & (df_six_sample['Immune cell']=='gdT-cell')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_c"})
df_gdT_d = df_six_sample[(df_six_sample['Donor']=='d') & (df_six_sample['Immune cell']=='gdT-cell')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_d"})
df_gdT_e = df_six_sample[(df_six_sample['Donor']=='e') & (df_six_sample['Immune cell']=='gdT-cell')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_e"})
df_gdT_f = df_six_sample[(df_six_sample['Donor']=='f') & (df_six_sample['Immune cell']=='gdT-cell')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_f"})

df_gdT = df_gdT_a.copy()
df_gdT = df_gdT.merge(df_gdT_b, on='Gene Stable ID')
df_gdT = df_gdT.merge(df_gdT_c, on='Gene Stable ID')
df_gdT = df_gdT.merge(df_gdT_d, on='Gene Stable ID')
df_gdT = df_gdT.merge(df_gdT_e, on='Gene Stable ID')
df_gdT = df_gdT.merge(df_gdT_f, on='Gene Stable ID')
df_gdT

Gene Stable ID    TPM_a    TPM_b    TPM_c    TPM_d    TPM_e    TPM_f
0      ENSG00000000003   0.6627   0.3322   0.0919   0.4343   0.1148   0.4878
1      ENSG00000000005   0.0000   0.0000   0.0000   0.0000   0.0000   0.0000
2      ENSG00000000419  26.5745  13.4640  12.6375  20.8420  14.5859  18.5510
3      ENSG00000000457   4.1022   6.5592   6.7440  10.9271   3.3378   9.5669
4      ENSG00000000460   0.4132   0.9894   0.8762   0.7138   0.9272   0.4436
...                ...      ...      ...      ...      ...      ...      ...
20157  ENSG00000291313   3.7523  13.7884   2.0915   3.4601   5.0461   6.6159
20158  ENSG00000291314   0.0000   0.0000   0.0000   0.0000   0.0000   0.0000
20159  ENSG00000291315   0.0000   0.0000   0.0000   0.0000   0.0000   0.0000
20160  ENSG00000291316   0.9053   0.9892   1.4828   1.3407   0.1994   2.0291
20161  ENSG00000291317   6.2835   9.3394  11.2962  14.2701   3.4812   8.8542

[20162 rows x 7 columns]

In [20]:
df_myeloid_a = df_six_sample[(df_six_sample['Donor']=='a') & (df_six_sample['Immune cell']=='myeloid DC')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_a"})
df_myeloid_b = df_six_sample[(df_six_sample['Donor']=='b') & (df_six_sample['Immune cell']=='myeloid DC')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_b"})
df_myeloid_c = df_six_sample[(df_six_sample['Donor']=='c') & (df_six_sample['Immune cell']=='myeloid DC')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_c"})
df_myeloid_d = df_six_sample[(df_six_sample['Donor']=='d') & (df_six_sample['Immune cell']=='myeloid DC')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_d"})
df_myeloid_e = df_six_sample[(df_six_sample['Donor']=='e') & (df_six_sample['Immune cell']=='myeloid DC')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_e"})

df_myeloid = df_myeloid_a.copy()
df_myeloid = df_myeloid.merge(df_myeloid_b, on='Gene Stable ID')
df_myeloid = df_myeloid.merge(df_myeloid_c, on='Gene Stable ID')
df_myeloid = df_myeloid.merge(df_myeloid_d, on='Gene Stable ID')
df_myeloid = df_myeloid.merge(df_myeloid_e, on='Gene Stable ID')
df_myeloid

Gene Stable ID    TPM_a    TPM_b    TPM_c    TPM_d    TPM_e
0      ENSG00000000003   0.0386   0.0327   0.0000   0.0273   0.0229
1      ENSG00000000005   0.0000   0.0000   0.0000   0.0000   0.0000
2      ENSG00000000419  27.1166  15.4658  13.4360  19.0300  15.6188
3      ENSG00000000457   4.4168   4.2593   4.5739   5.5440   3.0529
4      ENSG00000000460   0.7116   1.1337   1.8568   0.2753   1.2229
...                ...      ...      ...      ...      ...      ...
20157  ENSG00000291313   3.7705   9.2718   3.7397   3.6455   4.8038
20158  ENSG00000291314   0.0000   0.0000   0.0000   0.0000   0.0000
20159  ENSG00000291315   0.0000   0.0000   0.0000   0.0000   0.0000
20160  ENSG00000291316   0.6943   0.5390   1.7670   1.3278   0.2675
20161  ENSG00000291317   9.1207  11.6610   8.1984   9.2461  10.5007

[20162 rows x 6 columns]

In [21]:
df_plasmacytoid_a = df_six_sample[(df_six_sample['Donor']=='a') & (df_six_sample['Immune cell']=='plasmacytoid DC')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_a"})
df_plasmacytoid_b = df_six_sample[(df_six_sample['Donor']=='b') & (df_six_sample['Immune cell']=='plasmacytoid DC')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_b"})
df_plasmacytoid_c = df_six_sample[(df_six_sample['Donor']=='c') & (df_six_sample['Immune cell']=='plasmacytoid DC')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_c"})
df_plasmacytoid_d = df_six_sample[(df_six_sample['Donor']=='d') & (df_six_sample['Immune cell']=='plasmacytoid DC')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_d"})
df_plasmacytoid_e = df_six_sample[(df_six_sample['Donor']=='e') & (df_six_sample['Immune cell']=='plasmacytoid DC')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_e"})
df_plasmacytoid_f = df_six_sample[(df_six_sample['Donor']=='f') & (df_six_sample['Immune cell']=='plasmacytoid DC')][['ENSG ID', 'TPM']].reset_index(drop=True).rename(columns={"ENSG ID": "Gene Stable ID", "TPM": "TPM_f"})

df_plasmacytoid = df_plasmacytoid_a.copy()
df_plasmacytoid = df_plasmacytoid.merge(df_plasmacytoid_b, on='Gene Stable ID')
df_plasmacytoid = df_plasmacytoid.merge(df_plasmacytoid_c, on='Gene Stable ID')
df_plasmacytoid = df_plasmacytoid.merge(df_plasmacytoid_d, on='Gene Stable ID')
df_plasmacytoid = df_plasmacytoid.merge(df_plasmacytoid_e, on='Gene Stable ID')
df_plasmacytoid = df_plasmacytoid.merge(df_plasmacytoid_f, on='Gene Stable ID')
df_plasmacytoid

Gene Stable ID    TPM_a    TPM_b    TPM_c    TPM_d    TPM_e    TPM_f
0      ENSG00000000003   0.1008   0.0671   0.1652   0.1426   0.0286   0.1111
1      ENSG00000000005   0.0000   0.0000   0.0000   0.0000   0.0000   0.0000
2      ENSG00000000419  30.7273  16.4491  16.6766  10.5854  24.8711  20.1287
3      ENSG00000000457  16.2990   9.9592   8.1992   8.7379  11.4332   8.9219
4      ENSG00000000460   0.6260   0.1811   0.0528   0.0000   0.5654   0.7362
...                ...      ...      ...      ...      ...      ...      ...
20157  ENSG00000291313   3.1548  16.7163   4.1605   7.8298   5.0943   3.3031
20158  ENSG00000291314   0.0000   0.0000   0.0000   0.0000   0.0000   0.0000
20159  ENSG00000291315   0.0000   0.0000   0.0000   0.0000   0.0000   0.0000
20160  ENSG00000291316   1.7702   0.0000   0.6296   2.3097   1.1303   0.4889
20161  ENSG00000291317  21.0642  27.5094  26.7721  12.1787  21.2135  31.0536

[20162 rows x 7 columns]

In [22]:
# df_neutrophil, df_basophil, df_eosinophil, 
# df_classical_monocyte, df_intermediate_monocyte, df_non_classical_monocyte, 
# df_naive_CD8, df_memory_CD8, 
# df_Treg, df_naive_CD4, df_memory_CD4, 
# df_memory_B, df_naive_B, 
# df_NK, 
# df_MAIT, df_gdT, df_myeloid, df_plasmacytoid

In [23]:
import pandas as pd
import random

def choose_random_column_from_each_dataframe(*dataframes):
    random_columns = []
    for df in dataframes:
        if isinstance(df, pd.DataFrame) and not df.empty:
            column = random.choice(df.columns[1:])
            random_columns.append(column)
        else:
            random_columns.append(None)  # Add None if DataFrame is empty or not provided
    return random_columns

# Example usage:
random_columns = choose_random_column_from_each_dataframe(df_neutrophil, df_basophil, df_eosinophil, df_classical_monocyte, df_intermediate_monocyte, df_non_classical_monocyte, df_naive_CD8, df_memory_CD8, df_Treg, df_naive_CD4, df_memory_CD4, df_memory_B, df_naive_B, df_NK, df_MAIT, df_gdT, df_myeloid, df_plasmacytoid)
print(random_columns)

['TPM_c', 'TPM_f', 'TPM_f', 'TPM_a', 'TPM_e', 'TPM_c', 'TPM_e', 'TPM_f', 'TPM_c', 'TPM_d', 'TPM_e', 'TPM_f', 'TPM_e', 'TPM_c', 'TPM_f', 'TPM_f', 'TPM_c', 'TPM_f']


In [24]:
df_bulk = df_NK[['Gene Stable ID']].copy()
N = 10000   # N is the number of samples
y = np.zeros((N, 18))

for i in range(0, N):
    # choose random column from each dataframe
    random_columns = choose_random_column_from_each_dataframe(df_neutrophil, df_basophil, df_eosinophil, df_classical_monocyte, df_intermediate_monocyte, df_non_classical_monocyte, df_naive_CD8, df_memory_CD8, df_Treg, df_naive_CD4, df_memory_CD4, df_memory_B, df_naive_B, df_NK, df_MAIT, df_gdT, df_myeloid, df_plasmacytoid)
    # w is the weight of the recipe
    w = np.random.rand(18)
    w = w/sum(w)
    # mask is the 2d array of those selected columns
    mask = np.array([df_neutrophil[random_columns[0]], df_basophil[random_columns[1]], df_eosinophil[random_columns[2]], df_classical_monocyte[random_columns[3]], df_intermediate_monocyte[random_columns[4]], df_non_classical_monocyte[random_columns[5]], df_naive_CD8[random_columns[6]], df_memory_CD8[random_columns[7]], df_Treg[random_columns[8]], df_naive_CD4[random_columns[9]], df_memory_CD4[random_columns[10]], df_memory_B[random_columns[11]], df_naive_B[random_columns[12]], df_NK[random_columns[13]], df_MAIT[random_columns[14]], df_gdT[random_columns[15]], df_myeloid[random_columns[16]], df_plasmacytoid[random_columns[17]]]).T
    df_bulk['Sample '+str(i)] = np.sum(w*mask, axis=1)
    y[i] = w

/var/folders/5s/knl_q6l51sb6rhy0g4_v1bph0000gp/T/ipykernel_48774/4265928159.py:13: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_bulk['Sample '+str(i)] = np.sum(w*mask, axis=1)
/var/folders/5s/knl_q6l51sb6rhy0g4_v1bph0000gp/T/ipykernel_48774/4265928159.py:13: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_bulk['Sample '+str(i)] = np.sum(w*mask, axis=1)
/var/folders/5s/knl_q6l51sb6rhy0g4_v1bph0000gp/T/ipykernel_48774/4265928159.py:13: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling 

/var/folders/5s/knl_q6l51sb6rhy0g4_v1bph0000gp/T/ipykernel_48774/4265928159.py:13: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_bulk['Sample '+str(i)] = np.sum(w*mask, axis=1)
/var/folders/5s/knl_q6l51sb6rhy0g4_v1bph0000gp/T/ipykernel_48774/4265928159.py:13: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_bulk['Sample '+str(i)] = np.sum(w*mask, axis=1)
/var/folders/5s/knl_q6l51sb6rhy0g4_v1bph0000gp/T/ipykernel_48774/4265928159.py:13: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling 

/var/folders/5s/knl_q6l51sb6rhy0g4_v1bph0000gp/T/ipykernel_48774/4265928159.py:13: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_bulk['Sample '+str(i)] = np.sum(w*mask, axis=1)
/var/folders/5s/knl_q6l51sb6rhy0g4_v1bph0000gp/T/ipykernel_48774/4265928159.py:13: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_bulk['Sample '+str(i)] = np.sum(w*mask, axis=1)
/var/folders/5s/knl_q6l51sb6rhy0g4_v1bph0000gp/T/ipykernel_48774/4265928159.py:13: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling 

/var/folders/5s/knl_q6l51sb6rhy0g4_v1bph0000gp/T/ipykernel_48774/4265928159.py:13: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_bulk['Sample '+str(i)] = np.sum(w*mask, axis=1)
/var/folders/5s/knl_q6l51sb6rhy0g4_v1bph0000gp/T/ipykernel_48774/4265928159.py:13: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_bulk['Sample '+str(i)] = np.sum(w*mask, axis=1)
/var/folders/5s/knl_q6l51sb6rhy0g4_v1bph0000gp/T/ipykernel_48774/4265928159.py:13: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling 

/var/folders/5s/knl_q6l51sb6rhy0g4_v1bph0000gp/T/ipykernel_48774/4265928159.py:13: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_bulk['Sample '+str(i)] = np.sum(w*mask, axis=1)
/var/folders/5s/knl_q6l51sb6rhy0g4_v1bph0000gp/T/ipykernel_48774/4265928159.py:13: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_bulk['Sample '+str(i)] = np.sum(w*mask, axis=1)
/var/folders/5s/knl_q6l51sb6rhy0g4_v1bph0000gp/T/ipykernel_48774/4265928159.py:13: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling 

...

/var/folders/5s/knl_q6l51sb6rhy0g4_v1bph0000gp/T/ipykernel_48774/4265928159.py:13: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_bulk['Sample '+str(i)] = np.sum(w*mask, axis=1)
/var/folders/5s/knl_q6l51sb6rhy0g4_v1bph0000gp/T/ipykernel_48774/4265928159.py:13: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_bulk['Sample '+str(i)] = np.sum(w*mask, axis=1)
/var/folders/5s/knl_q6l51sb6rhy0g4_v1bph0000gp/T/ipykernel_48774/4265928159.py:13: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling 

/var/folders/5s/knl_q6l51sb6rhy0g4_v1bph0000gp/T/ipykernel_48774/4265928159.py:13: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_bulk['Sample '+str(i)] = np.sum(w*mask, axis=1)
/var/folders/5s/knl_q6l51sb6rhy0g4_v1bph0000gp/T/ipykernel_48774/4265928159.py:13: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_bulk['Sample '+str(i)] = np.sum(w*mask, axis=1)
/var/folders/5s/knl_q6l51sb6rhy0g4_v1bph0000gp/T/ipykernel_48774/4265928159.py:13: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling 

/var/folders/5s/knl_q6l51sb6rhy0g4_v1bph0000gp/T/ipykernel_48774/4265928159.py:13: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_bulk['Sample '+str(i)] = np.sum(w*mask, axis=1)
/var/folders/5s/knl_q6l51sb6rhy0g4_v1bph0000gp/T/ipykernel_48774/4265928159.py:13: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_bulk['Sample '+str(i)] = np.sum(w*mask, axis=1)
/var/folders/5s/knl_q6l51sb6rhy0g4_v1bph0000gp/T/ipykernel_48774/4265928159.py:13: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling 

/var/folders/5s/knl_q6l51sb6rhy0g4_v1bph0000gp/T/ipykernel_48774/4265928159.py:13: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_bulk['Sample '+str(i)] = np.sum(w*mask, axis=1)
/var/folders/5s/knl_q6l51sb6rhy0g4_v1bph0000gp/T/ipykernel_48774/4265928159.py:13: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_bulk['Sample '+str(i)] = np.sum(w*mask, axis=1)
/var/folders/5s/knl_q6l51sb6rhy0g4_v1bph0000gp/T/ipykernel_48774/4265928159.py:13: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling 

/var/folders/5s/knl_q6l51sb6rhy0g4_v1bph0000gp/T/ipykernel_48774/4265928159.py:13: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_bulk['Sample '+str(i)] = np.sum(w*mask, axis=1)
/var/folders/5s/knl_q6l51sb6rhy0g4_v1bph0000gp/T/ipykernel_48774/4265928159.py:13: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_bulk['Sample '+str(i)] = np.sum(w*mask, axis=1)
/var/folders/5s/knl_q6l51sb6rhy0g4_v1bph0000gp/T/ipykernel_48774/4265928159.py:13: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling 

In [25]:
X = df_bulk.iloc[:, 1:].values.T

In [26]:
from sklearn.feature_selection import SelectKBest
from sklearn.feature_selection import mutual_info_regression
from sklearn.svm import NuSVR
from sklearn.pipeline import Pipeline

In [27]:
# Create the pipeline with SelectKBest and mutual_info_regression
k = 10
pipeline = Pipeline([
    ('feature_selection', SelectKBest(mutual_info_regression, k=k)),
    ('regression', NuSVR())
])

# Split data into training and testing sets
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(X, y[:, 0], test_size=0.3, random_state=42)

# Fit the pipeline on the training data
pipeline.fit(X_train, y_train)

# Get the boolean mask of selected features
selected_mask = pipeline.named_steps['feature_selection'].get_support()

# Get the indices of selected features
selected_indices = np.where(selected_mask)[0]

# Get the names of selected features (assuming you have feature names available)
feature_names = [f'Feature_{i}' for i in range(X.shape[1])]  # Replace this with your actual feature names

selected_features = [feature_names[i] for i in selected_indices]

print("Selected Features:", selected_features)

Selected Features: ['Feature_4397', 'Feature_5386', 'Feature_5528', 'Feature_5633', 'Feature_6597', 'Feature_10642', 'Feature_10726', 'Feature_12352', 'Feature_18823', 'Feature_18837']


In [28]:
# Create the pipeline with SelectKBest and mutual_info_regression
k = 10
pipeline = Pipeline([
    ('feature_selection', SelectKBest(mutual_info_regression, k=k)),
    ('regression', NuSVR())
])

# Split data into training and testing sets
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(X, y[:, 1], test_size=0.3, random_state=42)

# Fit the pipeline on the training data
pipeline.fit(X_train, y_train)

# Get the boolean mask of selected features
selected_mask = pipeline.named_steps['feature_selection'].get_support()

# Get the indices of selected features
selected_indices = np.where(selected_mask)[0]

# Get the names of selected features (assuming you have feature names available)
feature_names = [f'Feature_{i}' for i in range(X.shape[1])]  # Replace this with your actual feature names

selected_features = [feature_names[i] for i in selected_indices]

print("Selected Features:", selected_features)

Selected Features: ['Feature_80', 'Feature_2030', 'Feature_5530', 'Feature_7691', 'Feature_7819', 'Feature_9082', 'Feature_9085', 'Feature_10931', 'Feature_12978', 'Feature_16058']


In [29]:
# Create the pipeline with SelectKBest and mutual_info_regression
k = 10
pipeline = Pipeline([
    ('feature_selection', SelectKBest(mutual_info_regression, k=k)),
    ('regression', NuSVR())
])

# Split data into training and testing sets
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(X, y[:, 2], test_size=0.3, random_state=42)

# Fit the pipeline on the training data
pipeline.fit(X_train, y_train)

# Get the boolean mask of selected features
selected_mask = pipeline.named_steps['feature_selection'].get_support()

# Get the indices of selected features
selected_indices = np.where(selected_mask)[0]

# Get the names of selected features (assuming you have feature names available)
feature_names = [f'Feature_{i}' for i in range(X.shape[1])]  # Replace this with your actual feature names

selected_features = [feature_names[i] for i in selected_indices]

print("Selected Features:", selected_features)

Selected Features: ['Feature_1941', 'Feature_2782', 'Feature_3057', 'Feature_5429', 'Feature_9933', 'Feature_10470', 'Feature_12088', 'Feature_17402', 'Feature_17988', 'Feature_19563']


In [30]:
# Create the pipeline with SelectKBest and mutual_info_regression
k = 10
pipeline = Pipeline([
    ('feature_selection', SelectKBest(mutual_info_regression, k=k)),
    ('regression', NuSVR())
])

# Split data into training and testing sets
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(X, y[:, 3], test_size=0.3, random_state=42)

# Fit the pipeline on the training data
pipeline.fit(X_train, y_train)

# Get the boolean mask of selected features
selected_mask = pipeline.named_steps['feature_selection'].get_support()

# Get the indices of selected features
selected_indices = np.where(selected_mask)[0]

# Get the names of selected features (assuming you have feature names available)
feature_names = [f'Feature_{i}' for i in range(X.shape[1])]  # Replace this with your actual feature names

selected_features = [feature_names[i] for i in selected_indices]

print("Selected Features:", selected_features)

Selected Features: ['Feature_2122', 'Feature_2130', 'Feature_2931', 'Feature_3535', 'Feature_5205', 'Feature_7361', 'Feature_15489', 'Feature_15679', 'Feature_18249', 'Feature_18979']


In [31]:
# Create the pipeline with SelectKBest and mutual_info_regression
k = 10
pipeline = Pipeline([
    ('feature_selection', SelectKBest(mutual_info_regression, k=k)),
    ('regression', NuSVR())
])

# Split data into training and testing sets
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(X, y[:, 4], test_size=0.3, random_state=42)

# Fit the pipeline on the training data
pipeline.fit(X_train, y_train)

# Get the boolean mask of selected features
selected_mask = pipeline.named_steps['feature_selection'].get_support()

# Get the indices of selected features
selected_indices = np.where(selected_mask)[0]

# Get the names of selected features (assuming you have feature names available)
feature_names = [f'Feature_{i}' for i in range(X.shape[1])]  # Replace this with your actual feature names

selected_features = [feature_names[i] for i in selected_indices]

print("Selected Features:", selected_features)

Selected Features: ['Feature_141', 'Feature_6278', 'Feature_8671', 'Feature_10368', 'Feature_10649', 'Feature_11397', 'Feature_13186', 'Feature_15163', 'Feature_16618', 'Feature_19019']


In [32]:
# Create the pipeline with SelectKBest and mutual_info_regression
k = 10
pipeline = Pipeline([
    ('feature_selection', SelectKBest(mutual_info_regression, k=k)),
    ('regression', NuSVR())
])

# Split data into training and testing sets
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(X, y[:, 5], test_size=0.3, random_state=42)

# Fit the pipeline on the training data
pipeline.fit(X_train, y_train)

# Get the boolean mask of selected features
selected_mask = pipeline.named_steps['feature_selection'].get_support()

# Get the indices of selected features
selected_indices = np.where(selected_mask)[0]

# Get the names of selected features (assuming you have feature names available)
feature_names = [f'Feature_{i}' for i in range(X.shape[1])]  # Replace this with your actual feature names

selected_features = [feature_names[i] for i in selected_indices]

print("Selected Features:", selected_features)

Selected Features: ['Feature_143', 'Feature_655', 'Feature_1056', 'Feature_4690', 'Feature_8112', 'Feature_8776', 'Feature_9534', 'Feature_11652', 'Feature_16991', 'Feature_17399']


In [33]:
# Create the pipeline with SelectKBest and mutual_info_regression
k = 10
pipeline = Pipeline([
    ('feature_selection', SelectKBest(mutual_info_regression, k=k)),
    ('regression', NuSVR())
])

# Split data into training and testing sets
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(X, y[:, 6], test_size=0.3, random_state=42)

# Fit the pipeline on the training data
pipeline.fit(X_train, y_train)

# Get the boolean mask of selected features
selected_mask = pipeline.named_steps['feature_selection'].get_support()

# Get the indices of selected features
selected_indices = np.where(selected_mask)[0]

# Get the names of selected features (assuming you have feature names available)
feature_names = [f'Feature_{i}' for i in range(X.shape[1])]  # Replace this with your actual feature names

selected_features = [feature_names[i] for i in selected_indices]

print("Selected Features:", selected_features)

Selected Features: ['Feature_866', 'Feature_3216', 'Feature_6755', 'Feature_11377', 'Feature_12612', 'Feature_13529', 'Feature_15616', 'Feature_16549', 'Feature_16567', 'Feature_17961']


In [34]:
# Create the pipeline with SelectKBest and mutual_info_regression
k = 10
pipeline = Pipeline([
    ('feature_selection', SelectKBest(mutual_info_regression, k=k)),
    ('regression', NuSVR())
])

# Split data into training and testing sets
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(X, y[:, 7], test_size=0.3, random_state=42)

# Fit the pipeline on the training data
pipeline.fit(X_train, y_train)

# Get the boolean mask of selected features
selected_mask = pipeline.named_steps['feature_selection'].get_support()

# Get the indices of selected features
selected_indices = np.where(selected_mask)[0]

# Get the names of selected features (assuming you have feature names available)
feature_names = [f'Feature_{i}' for i in range(X.shape[1])]  # Replace this with your actual feature names

selected_features = [feature_names[i] for i in selected_indices]

print("Selected Features:", selected_features)

Selected Features: ['Feature_4928', 'Feature_9101', 'Feature_9611', 'Feature_9947', 'Feature_11058', 'Feature_14480', 'Feature_14823', 'Feature_14993', 'Feature_15593', 'Feature_16526']


In [35]:
# Create the pipeline with SelectKBest and mutual_info_regression
k = 10
pipeline = Pipeline([
    ('feature_selection', SelectKBest(mutual_info_regression, k=k)),
    ('regression', NuSVR())
])

# Split data into training and testing sets
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(X, y[:, 8], test_size=0.3, random_state=42)

# Fit the pipeline on the training data
pipeline.fit(X_train, y_train)

# Get the boolean mask of selected features
selected_mask = pipeline.named_steps['feature_selection'].get_support()

# Get the indices of selected features
selected_indices = np.where(selected_mask)[0]

# Get the names of selected features (assuming you have feature names available)
feature_names = [f'Feature_{i}' for i in range(X.shape[1])]  # Replace this with your actual feature names

selected_features = [feature_names[i] for i in selected_indices]

print("Selected Features:", selected_features)

Selected Features: ['Feature_257', 'Feature_663', 'Feature_7503', 'Feature_12004', 'Feature_14563', 'Feature_14765', 'Feature_16974', 'Feature_18102', 'Feature_18309', 'Feature_20007']


In [36]:
# Create the pipeline with SelectKBest and mutual_info_regression
k = 10
pipeline = Pipeline([
    ('feature_selection', SelectKBest(mutual_info_regression, k=k)),
    ('regression', NuSVR())
])

# Split data into training and testing sets
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(X, y[:, 9], test_size=0.3, random_state=42)

# Fit the pipeline on the training data
pipeline.fit(X_train, y_train)

# Get the boolean mask of selected features
selected_mask = pipeline.named_steps['feature_selection'].get_support()

# Get the indices of selected features
selected_indices = np.where(selected_mask)[0]

# Get the names of selected features (assuming you have feature names available)
feature_names = [f'Feature_{i}' for i in range(X.shape[1])]  # Replace this with your actual feature names

selected_features = [feature_names[i] for i in selected_indices]

print("Selected Features:", selected_features)

Selected Features: ['Feature_6960', 'Feature_7034', 'Feature_7770', 'Feature_9415', 'Feature_14270', 'Feature_15330', 'Feature_15965', 'Feature_19682', 'Feature_19846', 'Feature_19860']


In [37]:
# Create the pipeline with SelectKBest and mutual_info_regression
k = 10
pipeline = Pipeline([
    ('feature_selection', SelectKBest(mutual_info_regression, k=k)),
    ('regression', NuSVR())
])

# Split data into training and testing sets
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(X, y[:, 10], test_size=0.3, random_state=42)

# Fit the pipeline on the training data
pipeline.fit(X_train, y_train)

# Get the boolean mask of selected features
selected_mask = pipeline.named_steps['feature_selection'].get_support()

# Get the indices of selected features
selected_indices = np.where(selected_mask)[0]

# Get the names of selected features (assuming you have feature names available)
feature_names = [f'Feature_{i}' for i in range(X.shape[1])]  # Replace this with your actual feature names

selected_features = [feature_names[i] for i in selected_indices]

print("Selected Features:", selected_features)

Selected Features: ['Feature_3186', 'Feature_6623', 'Feature_7594', 'Feature_8177', 'Feature_8501', 'Feature_10373', 'Feature_11851', 'Feature_15619', 'Feature_16796', 'Feature_17230']


In [38]:
# Create the pipeline with SelectKBest and mutual_info_regression
k = 10
pipeline = Pipeline([
    ('feature_selection', SelectKBest(mutual_info_regression, k=k)),
    ('regression', NuSVR())
])

# Split data into training and testing sets
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(X, y[:, 11], test_size=0.3, random_state=42)

# Fit the pipeline on the training data
pipeline.fit(X_train, y_train)

# Get the boolean mask of selected features
selected_mask = pipeline.named_steps['feature_selection'].get_support()

# Get the indices of selected features
selected_indices = np.where(selected_mask)[0]

# Get the names of selected features (assuming you have feature names available)
feature_names = [f'Feature_{i}' for i in range(X.shape[1])]  # Replace this with your actual feature names

selected_features = [feature_names[i] for i in selected_indices]

print("Selected Features:", selected_features)

Selected Features: ['Feature_2735', 'Feature_3387', 'Feature_4493', 'Feature_4705', 'Feature_7412', 'Feature_9018', 'Feature_14233', 'Feature_14548', 'Feature_17080', 'Feature_18664']


In [39]:
# Create the pipeline with SelectKBest and mutual_info_regression
k = 10
pipeline = Pipeline([
    ('feature_selection', SelectKBest(mutual_info_regression, k=k)),
    ('regression', NuSVR())
])

# Split data into training and testing sets
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(X, y[:, 12], test_size=0.3, random_state=42)

# Fit the pipeline on the training data
pipeline.fit(X_train, y_train)

# Get the boolean mask of selected features
selected_mask = pipeline.named_steps['feature_selection'].get_support()

# Get the indices of selected features
selected_indices = np.where(selected_mask)[0]

# Get the names of selected features (assuming you have feature names available)
feature_names = [f'Feature_{i}' for i in range(X.shape[1])]  # Replace this with your actual feature names

selected_features = [feature_names[i] for i in selected_indices]

print("Selected Features:", selected_features)

Selected Features: ['Feature_272', 'Feature_1199', 'Feature_1956', 'Feature_4778', 'Feature_8044', 'Feature_11312', 'Feature_11859', 'Feature_14496', 'Feature_17694', 'Feature_18060']


In [40]:
# Create the pipeline with SelectKBest and mutual_info_regression
k = 10
pipeline = Pipeline([
    ('feature_selection', SelectKBest(mutual_info_regression, k=k)),
    ('regression', NuSVR())
])

# Split data into training and testing sets
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(X, y[:, 13], test_size=0.3, random_state=42)

# Fit the pipeline on the training data
pipeline.fit(X_train, y_train)

# Get the boolean mask of selected features
selected_mask = pipeline.named_steps['feature_selection'].get_support()

# Get the indices of selected features
selected_indices = np.where(selected_mask)[0]

# Get the names of selected features (assuming you have feature names available)
feature_names = [f'Feature_{i}' for i in range(X.shape[1])]  # Replace this with your actual feature names

selected_features = [feature_names[i] for i in selected_indices]

print("Selected Features:", selected_features)

Selected Features: ['Feature_5656', 'Feature_9874', 'Feature_10582', 'Feature_11311', 'Feature_13244', 'Feature_14783', 'Feature_15820', 'Feature_16006', 'Feature_16831', 'Feature_18887']


In [41]:
# Create the pipeline with SelectKBest and mutual_info_regression
k = 10
pipeline = Pipeline([
    ('feature_selection', SelectKBest(mutual_info_regression, k=k)),
    ('regression', NuSVR())
])

# Split data into training and testing sets
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(X, y[:, 14], test_size=0.3, random_state=42)

# Fit the pipeline on the training data
pipeline.fit(X_train, y_train)

# Get the boolean mask of selected features
selected_mask = pipeline.named_steps['feature_selection'].get_support()

# Get the indices of selected features
selected_indices = np.where(selected_mask)[0]

# Get the names of selected features (assuming you have feature names available)
feature_names = [f'Feature_{i}' for i in range(X.shape[1])]  # Replace this with your actual feature names

selected_features = [feature_names[i] for i in selected_indices]

print("Selected Features:", selected_features)

Selected Features: ['Feature_5345', 'Feature_8420', 'Feature_9027', 'Feature_10670', 'Feature_11115', 'Feature_12587', 'Feature_13008', 'Feature_17644', 'Feature_18266', 'Feature_19062']


In [42]:
# Create the pipeline with SelectKBest and mutual_info_regression
k = 10
pipeline = Pipeline([
    ('feature_selection', SelectKBest(mutual_info_regression, k=k)),
    ('regression', NuSVR())
])

# Split data into training and testing sets
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(X, y[:, 15], test_size=0.3, random_state=42)

# Fit the pipeline on the training data
pipeline.fit(X_train, y_train)

# Get the boolean mask of selected features
selected_mask = pipeline.named_steps['feature_selection'].get_support()

# Get the indices of selected features
selected_indices = np.where(selected_mask)[0]

# Get the names of selected features (assuming you have feature names available)
feature_names = [f'Feature_{i}' for i in range(X.shape[1])]  # Replace this with your actual feature names

selected_features = [feature_names[i] for i in selected_indices]

print("Selected Features:", selected_features)

Selected Features: ['Feature_3728', 'Feature_5587', 'Feature_9681', 'Feature_13944', 'Feature_15895', 'Feature_17615', 'Feature_18973', 'Feature_19014', 'Feature_19875', 'Feature_20146']


In [43]:
# Create the pipeline with SelectKBest and mutual_info_regression
k = 10
pipeline = Pipeline([
    ('feature_selection', SelectKBest(mutual_info_regression, k=k)),
    ('regression', NuSVR())
])

# Split data into training and testing sets
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(X, y[:, 16], test_size=0.3, random_state=42)

# Fit the pipeline on the training data
pipeline.fit(X_train, y_train)

# Get the boolean mask of selected features
selected_mask = pipeline.named_steps['feature_selection'].get_support()

# Get the indices of selected features
selected_indices = np.where(selected_mask)[0]

# Get the names of selected features (assuming you have feature names available)
feature_names = [f'Feature_{i}' for i in range(X.shape[1])]  # Replace this with your actual feature names

selected_features = [feature_names[i] for i in selected_indices]

print("Selected Features:", selected_features)

Selected Features: ['Feature_3563', 'Feature_4071', 'Feature_9465', 'Feature_10006', 'Feature_10771', 'Feature_12184', 'Feature_13251', 'Feature_13724', 'Feature_14747', 'Feature_19107']


In [44]:
# Create the pipeline with SelectKBest and mutual_info_regression
k = 10
pipeline = Pipeline([
    ('feature_selection', SelectKBest(mutual_info_regression, k=k)),
    ('regression', NuSVR())
])

# Split data into training and testing sets
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(X, y[:, 17], test_size=0.3, random_state=42)

# Fit the pipeline on the training data
pipeline.fit(X_train, y_train)

# Get the boolean mask of selected features
selected_mask = pipeline.named_steps['feature_selection'].get_support()

# Get the indices of selected features
selected_indices = np.where(selected_mask)[0]

# Get the names of selected features (assuming you have feature names available)
feature_names = [f'Feature_{i}' for i in range(X.shape[1])]  # Replace this with your actual feature names

selected_features = [feature_names[i] for i in selected_indices]

print("Selected Features:", selected_features)

Selected Features: ['Feature_3034', 'Feature_5256', 'Feature_6114', 'Feature_7261', 'Feature_8047', 'Feature_11239', 'Feature_13786', 'Feature_15108', 'Feature_15352', 'Feature_15407']
